### Importación e instalación de librerías 

In [ ]:
import numpy as np
import pandas as pd

import os 
import re
import json
import geopy
import folium
import statistics

from google.colab import drive
from folium.plugins import HeatMap
from folium.plugins import FloatImage
from folium.plugins import HeatMapWithTime
from folium.features import ColorLine
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter

from skimage.transform import resize
from more_itertools import sort_together 

import urllib, urllib.parse, urllib.request

In [ ]:
!pip install geopandas
import geopandas as gpd

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.0 MB 8.8 MB/s 
     |████████████████████████████████| 16.7 MB 529 kB/s 
     |████████████████████████████████| 6.3 MB 46.8 MB/s 


In [ ]:
!pip install geocoder
import geocoder

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 98 kB 4.8 MB/s 


In [ ]:
!pip install iteration_utilities

import iteration_utilities

from iteration_utilities import duplicates
from iteration_utilities import unique_everseen

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 283 kB 7.9 MB/s 


In [ ]:
drive.mount('/content/drive') 

dic_actual=os.chdir('/content/drive/My Drive/Folium/CDMX') 
dic=os.listdir(dic_actual)
print(dic)

Mounted at /content/drive
['Sectores.geojson', 'Cuadrantes.geojson', 'Alcadiasv1.GEOJSON', 'ID_alcaldias_datos.csv', 'DatosV1_D.csv', 'Alcaldias_ID.csv', 'geckodriver.log', 'F-CDMX.ipynb', 'F-CDMX-V1-L.ipynb', 'mapa_ejemplo_coropleta.html', 'mapa_ejemplo_calor.html', 'mapa_ejemplo_cor.html', 'Prueba link.gsheet', 'F-CDMX-V1-N.ipynb']


### Creación de poligonos espesificos dentro de los mapas 

In [ ]:
url = ('https://raw.githubusercontent.com/SECOORA/static_assets/'
       'master/maps/img/rose.png')
# agregar logoPM

color1 = {'fillColor': '#536878', 'color': '#536878','weight': 1}
color2 = {'fillColor': '#49678d', 'color': '#49678d','weight': 2}
color3 = {'fillColor': '#3e5f8a', 'color': '#3e5f8a','weight': 3}
tiles = [None,"Stamen Terrain","openstreetmap","Stamen Toner","cartodbpositron"]

def mapas(tile,cuadrante,sector,alcaldia):
  m = folium.Map(location=[19.4326018,-99.1332049],zoom_start=11,tiles=tile)
  FloatImage(url, bottom=70, left=75).add_to(m)

  draw = folium.plugins.Draw(export=True)
  draw.add_to(m)

  fs = folium.plugins.Fullscreen()
  m.add_child(fs)

  minimap = folium.plugins.MiniMap()
  m.add_child(minimap)

  with open('Cuadrantes.geojson', encoding='utf-8-sig') as f:
    dic_c = json.load(f)
  with open('Sectores.geojson', encoding='utf-8-sig') as f:
    dic_s = json.load(f)
  with open('Alcadiasv1.GEOJSON', encoding='utf-8-sig') as f:
    dic_a = json.load(f)

  if cuadrante == True:
    folium.GeoJson(dic_c, name="Cgeojson",style_function=lambda x:color1).add_to(m)
  if sector == True:
    folium.GeoJson(dic_s, name="Sgeojson",style_function=lambda x:color2).add_to(m) 
  if alcaldia == True:
    folium.GeoJson(dic_a, name="Ageojson",style_function=lambda x:color3).add_to(m)  
    
  return m,dic_c,dic_s,dic_a

In [ ]:
mapa,a,b,c=mapas(tiles[4],cuadrante=True,sector=True,alcaldia=True)
mapa

Output hidden; open in https://colab.research.google.com to view.

Posiblemente añadir el mapa de google drive o google earth 

### Agregar puntos a travez de una dirección o cordendas

In [ ]:
def cor_direc(direccion,cordenadas,ip):

  geolocator = Nominatim(user_agent="geoapiExercises")

  if direccion == True: 
    print('Indroduce la dirección') #Prolongación Guadalupe Victoria,Los Reyes, Xochimilco, Ciudad de México
    lugar=input()

    localizacion = geolocator.geocode(lugar, timeout=2, exactly_one=False)
    localizacion=list(localizacion[0][1])

    return localizacion,lugar
    
  if cordenadas == True:
    print('Indroduce cordendas (Latitud,Lognitud)') #19.433726197085818, -99.17520267747044
    cordenadas=input()

    direc = geolocator.reverse(cordenadas)
    direc=direc[0]

    return direc,cordenadas

  if ip == True:
    print('Indroduce la dirección IP')
    ip=input()

    ip = geocoder.ip(ip) #checar que las cordendas vacias nos vevuelvan un entorno vacio
    direccion=ip[0]
    coor_ip=ip.latlng

    return coor_ip,ip
  return 

In [ ]:
cor_direc(True,False,False)

Indroduce la dirección
Prolongación Guadalupe Victoria,Los Reyes, Xochimilco, Ciudad de México


([19.2486949, -99.0546151],
 'Prolongación Guadalupe Victoria,Los Reyes, Xochimilco, Ciudad de México')

#### Agregar cordenadas en el mapa

In [ ]:
def mapas_puntos(direccion,cordenadas,ip,tile,m_c,m_s,m_a):
  cor,det=cor_direc(direccion,cordenadas,ip)
  mapa,a,b,c=mapas(tile,m_c,m_s,m_a)
  folium.Marker(location=cor,popup=str(det)+'\n'+str(cor), icon=folium.Icon(color="blue",icon="glyphicon glyphicon-flag"), ).add_to(mapa)
  return mapa

In [ ]:
mapas_puntos(False,False,True,tiles[2],m_c=True,m_s=True,m_a=True)

Output hidden; open in https://colab.research.google.com to view.

### Agregar el dataframe para realizar posicionmiento de analisis de los eventos

In [ ]:
df = pd.read_csv("DatosV1_D.csv")

df_alcaldia= pd.read_csv("Alcaldias_ID.csv")
df_alcaldia.drop(['UUID','CREADO_POR','FECHA_CREACION','MODIFICADO_POR','FECHA_MODIFICACION','VISIBLE','ID_ESTADO'], axis = 'columns', inplace=True)
df_alcaldia = df_alcaldia.drop_duplicates(subset=['ID_MUNICIPIO']) # alcaldias y su ID

id=df_alcaldia['ID_MUNICIPIO'].tolist()
al=df_alcaldia['NOMBRE_MUNICIPIO'].tolist()
for j in range(len(al)):
  df.loc[df['ID_MUNICIPIO'] == id[j],'ID_MUNICIPIO'] = al[j] 

### Función para filtrar datos y obtener las cordenadas 

In [ ]:
def datos_fil(df): 
  print('Listas a filtrar:',list(df.columns.values))
  print('Seleccione la lista a filtrar:')

  l_des=str(input())
  lista_p=df[l_des].tolist()

  def elem_unicos(l_des):

    l_unicos=list(dict.fromkeys(df[l_des].tolist()))
    l_unicos = [x for x in l_unicos if pd.isnull(x) == False]
    print('Elementos unicos de la lista:',l_unicos)

    return l_unicos
  elem_unicos(l_des)

  print('Patron a encontrar:')
  patron=str(input())
  lista_d= []

  for i in range(len(lista_p)):
    restul=re.match(patron, str(lista_p[i]))
    lista_d.append(restul)

  ind = 0
  lista_index=[]

  for i in range(len(lista_d)):
    ind +=1
    if lista_d[i] != None:
      lista_index.append(ind-1)
      
  ind=0
  index=lista_index

  return index 

In [ ]:
def mapas_cor(df,til,geo_s,geo_c,geo_a):

  index=datos_fil(df)
  m,dic_c,dic_s,dic_a=mapas(til,geo_s,geo_c,geo_a)

  df_f=df.iloc[index, :]
  lad=df_f['LATITUD'].tolist()
  log=df_f['LONGITUD'].tolist()

  cor=[lad,log]
  folium.LayerControl().add_to(m)

  for i in range(len(lad)):
    folium.Marker(location=[lad[i], log[i]]
                  ,popup="ID_EVENTO:"+str(df['ID_EVENTO'].tolist()[index[i]])+"\n"+"LUGAR:"+str(df['LUGAR'].tolist()[index[i]])
                  ,icon=folium.Icon(icon="remove"), ).add_to(m)
  
  mapa.save('mapa_ejemplo_cor.html')

  return m

In [ ]:
mapa=mapas_cor(df,tiles[4],geo_s=True,geo_c=False,geo_a=False)
mapa

Listas a filtrar: ['Unnamed: 0', 'ID_EVENTO', 'ID_DIRECCION_EVENTO', 'ID_COLONIA', 'ID_MUNICIPIO', 'ID_ESTADO', 'LATITUD', 'LONGITUD', 'LUGAR', 'CALLE', 'CODIGO_POSTAL', 'ID_PERSONA_INVOLUCRADA', 'NOMBRE', 'APELLIDO_PATERNO', 'APELLIDO_MATERNO', 'SEXO', 'EDAD', 'FECHA_MODIFICACION', 'ID_TIPO_PERSONA', 'ID_PERSONA_ORIGEN', 'ID_DESCRIPCION_EVENTO', 'FECHA_DESCRIPCION', 'DESCRIPCION', 'ID_OBJETO_INVOLUCRADO', 'OBSERVACIONES', 'ID_OBJETO', 'CANTIDAD', 'VALOR_ESTIMADO', 'ID_VEHICULO_INVOLUCRADO', 'NUMERO_PLACA', 'SENIAS_PARTICULARES', 'ID_COLOR', 'ID_TIPO_VEHICULO', 'ID_ESTADO_ORIGEN', 'ID_VEHICULO_ORIGEN', 'ID_USO_VEHICULO', 'ID_ESTADO_FISICO_VEHICULO', 'NUMERO_TELEFONO', 'FOLIO', 'ID_DISPOSITIVO', 'FECHA_INICIO', 'FECHA_FIN', 'ID_MOTIVO', 'PRIORIDAD', 'FECHA_EVENTO']
Seleccione la lista a filtrar:
CALLE
Elementos unicos de la lista: ['LAGO DE FONDO', 'MIGUEL NEGRETE', 'CERRADA SANTA LUCÍA', 'PUENTE DE LA GLORIA', 'CALLE 4', 'TOLTECAS', 'TESORO', 'FRANCISCO SARABIA', 'RETORNO PRIMERO CASA 

In [ ]:
def mapas_calor(df,til,geo_s,geo_c,geo_a):
  
  index=datos_fil(df)
  m,dic_c,dic_s,dic_a=mapas(til,geo_s,geo_c,geo_a)

  df_f=df.iloc[index, :]
  lad=df_f['LATITUD'].tolist()
  log=df_f['LONGITUD'].tolist()

  cor=[lad,log]
  vec=[1]*len(lad)

  mapa_calor = HeatMap( list(zip(lad, log, vec)),
                      name="Datos",
                      min_opacity=0.2,
                      max_val=max(vec),
                      radius=20, 
                      blur=30, 
                      max_zoom=1)
  mapa_calor.add_to(m)

  mapa.save('mapa_ejemplo_calor.html')
  
  return m

In [ ]:
mapas=mapas_calor(df,tiles[4],geo_s=False,geo_c=True,geo_a=True)
mapas

Listas a filtrar: ['Unnamed: 0', 'ID_EVENTO', 'ID_DIRECCION_EVENTO', 'ID_COLONIA', 'ID_MUNICIPIO', 'ID_ESTADO', 'LATITUD', 'LONGITUD', 'LUGAR', 'CALLE', 'CODIGO_POSTAL', 'ID_PERSONA_INVOLUCRADA', 'NOMBRE', 'APELLIDO_PATERNO', 'APELLIDO_MATERNO', 'SEXO', 'EDAD', 'FECHA_MODIFICACION', 'ID_TIPO_PERSONA', 'ID_PERSONA_ORIGEN', 'ID_DESCRIPCION_EVENTO', 'FECHA_DESCRIPCION', 'DESCRIPCION', 'ID_OBJETO_INVOLUCRADO', 'OBSERVACIONES', 'ID_OBJETO', 'CANTIDAD', 'VALOR_ESTIMADO', 'ID_VEHICULO_INVOLUCRADO', 'NUMERO_PLACA', 'SENIAS_PARTICULARES', 'ID_COLOR', 'ID_TIPO_VEHICULO', 'ID_ESTADO_ORIGEN', 'ID_VEHICULO_ORIGEN', 'ID_USO_VEHICULO', 'ID_ESTADO_FISICO_VEHICULO', 'NUMERO_TELEFONO', 'FOLIO', 'ID_DISPOSITIVO', 'FECHA_INICIO', 'FECHA_FIN', 'ID_MOTIVO', 'PRIORIDAD', 'FECHA_EVENTO']
Seleccione la lista a filtrar:
NOMBRE
Elementos unicos de la lista: ['VIOLETA', 'HELIBERTO', 'MARTIN JUAN', 'MARIA CHRISTINA', 'EULOGIO', 'MARIA SALUD', 'LAZARO', 'GREGORIO', 'JOAQUIN', 'ESTEFANY', 'IRMA', 'ARMANDO', 'CHRISTI

TypeError: ignored

## Mapas de coropleta

#### GeoJson y normalización

In [ ]:
#Agregación de los codigos de las alcaldías de CDMX 
df_alcaldia= pd.read_csv("Alcaldias_ID.csv")
df_alcaldia.drop(['UUID','CREADO_POR','FECHA_CREACION','MODIFICADO_POR','FECHA_MODIFICACION','VISIBLE','ID_ESTADO'], axis = 'columns', inplace=True)
df_alcaldia = df_alcaldia.drop_duplicates(subset=['ID_MUNICIPIO']) #alcaldias y su ID

with open('Alcadiasv1.GEOJSON', encoding='utf-8-sig') as f:
    dic_a = json.load(f)

from pandas.io.json import json_normalize

df_alcaldia_json = json_normalize(dic_a['features']) #Alcaldias cdmx para 

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  # This is added back by InteractiveShellApp.init_path()


#### Datos 

In [ ]:
id_alcaldia=[15,6,7,13,8,4,10,9,5,12,11,14,2,1,3,16]
fill_color=['BuGn', 'BuPu', 'GnBu', 'OrRd', 'PuBu', 'PuBuGn', 'PuRd', 'RdPu', 'YlGn', 'YlGnBu', 'YlOrBr','YlOrRd']
alcaldias=['ALVARO OBREGON','AZCAPOTZALCO','BENITO JUAREZ','COYOACAN',
           'CUAJIMALPA DE MORELOS','CUAUHTEMOC','GUSTAVO A. MADERO',
           'IZTACALCO','IZTAPALAPA','LA MAGDALENA CONTRERAS','MIGUEL HIDALGO',
           'MILPA ALTA','TLAHUAC','TLALPAN','VENUSTIANO CARRANZA','XOCHIMILCO']

def mapas_coropleta_mer(til,fill_color):
  index=datos_fil(df)

  df_f=df.iloc[index, :]
  freq = df_f.groupby(['ID_MUNICIPIO']).count() 
  datos_alc=freq['ID_EVENTO'].tolist()

  df_datos_alcc = pd.DataFrame()
  df_datos_alcc['TOTAL_EVENTOS'] = freq['ID_EVENTO'].tolist()
  df_datos_alcc['ALCALDIAS'] = list(freq.index)

  lista_iguales=list(set(list(freq.index)) ^ set(alcaldias))

  df_datos_alcc=df_datos_alcc.append([{'ALCALDIAS': x} for x in lista_iguales], ignore_index=True)
  df_datos_alcc=df_datos_alcc.fillna(0)

  for j in range(len(al)):
    df_datos_alcc.loc[df_datos_alcc['ALCALDIAS'] == alcaldias[j],'ID_MUNICIPIO'] = int(id_alcaldia[j])

  mapa,dic_c,dic_s,dic_a=mapas(til,False,False,False)

  folium.Choropleth(dic_a,
                    name='choropleth',
                    data=df_datos_alcc,
                    columns=['ID_MUNICIPIO','TOTAL_EVENTOS'],
                    key_on='properties.fid',
                    fill_color=fill_color,
                    fill_opacity=0.8,
                    line_opacity=1.0,
                    legend_name='Eventos por Alcaldía').add_to(mapa)

  folium.LayerControl().add_to(mapa)

  mapa.save('mapa_ejemplo_coropleta.html')

  return mapa

In [ ]:
mapa=mapas_coropleta_mer(tiles[4],fill_color[9])
mapa

Listas a filtrar: ['Unnamed: 0', 'ID_EVENTO', 'ID_DIRECCION_EVENTO', 'ID_COLONIA', 'ID_MUNICIPIO', 'ID_ESTADO', 'LATITUD', 'LONGITUD', 'LUGAR', 'CALLE', 'CODIGO_POSTAL', 'ID_PERSONA_INVOLUCRADA', 'NOMBRE', 'APELLIDO_PATERNO', 'APELLIDO_MATERNO', 'SEXO', 'EDAD', 'FECHA_MODIFICACION', 'ID_TIPO_PERSONA', 'ID_PERSONA_ORIGEN', 'ID_DESCRIPCION_EVENTO', 'FECHA_DESCRIPCION', 'DESCRIPCION', 'ID_OBJETO_INVOLUCRADO', 'OBSERVACIONES', 'ID_OBJETO', 'CANTIDAD', 'VALOR_ESTIMADO', 'ID_VEHICULO_INVOLUCRADO', 'NUMERO_PLACA', 'SENIAS_PARTICULARES', 'ID_COLOR', 'ID_TIPO_VEHICULO', 'ID_ESTADO_ORIGEN', 'ID_VEHICULO_ORIGEN', 'ID_USO_VEHICULO', 'ID_ESTADO_FISICO_VEHICULO', 'NUMERO_TELEFONO', 'FOLIO', 'ID_DISPOSITIVO', 'FECHA_INICIO', 'FECHA_FIN', 'ID_MOTIVO', 'PRIORIDAD', 'FECHA_EVENTO']
Seleccione la lista a filtrar:
PRIORIDAD
Elementos unicos de la lista: ['ALTA', 'BAJA', 'MEDIA']
Patron a encontrar:
ALTA


#### TimeMap

In [ ]:
ind = [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24]

def mapas_calor_time(til):
  index=datos_fil(df)
  df_f=df.iloc[index, :]

  df_time=pd.DataFrame()

  df_time['LATITUD'] = df_f['LATITUD'].tolist()
  df_time['LONGITUD'] = df_f['LONGITUD'].tolist()
  df_time['FECHA_EVENTO'] =df_f['FECHA_EVENTO'].tolist()
  df_time = df_time.dropna()

  df_time['FECHA_EVENTO'] = pd.to_datetime(df_time['FECHA_EVENTO']) 
  df_time=df_time.sort_values('FECHA_EVENTO')

  df_time_map = [ [ [row['LATITUD'],row['LONGITUD'] ] for index, row in df_time[df_time['FECHA_EVENTO'].apply(lambda x: x.day==j)].iterrows() ] for j in ind ]

  mapa,dic_c,dic_s,dic_a=mapas(til,False,False,False)

  HeatMapWithTime(df_time_map,
                  ind,
                  auto_play=True,
                  max_opacity=0.3).add_to(mapa)

  folium.plugins.Fullscreen(mapa)
  folium.LayerControl().add_to(mapa)

  mapa.save('mapa_ejemplo_time.html')

  return mapa

### Funcion mapeo

In [ ]:
mapa=mapas_cor(df,tiles[2],geo_s=False,geo_c=True,geo_a=False)
mapa

Listas a filtrar: ['Unnamed: 0', 'ID_EVENTO', 'ID_DIRECCION_EVENTO', 'ID_COLONIA', 'ID_MUNICIPIO', 'ID_ESTADO', 'LATITUD', 'LONGITUD', 'LUGAR', 'CALLE', 'CODIGO_POSTAL', 'ID_PERSONA_INVOLUCRADA', 'NOMBRE', 'APELLIDO_PATERNO', 'APELLIDO_MATERNO', 'SEXO', 'EDAD', 'FECHA_MODIFICACION', 'ID_TIPO_PERSONA', 'ID_PERSONA_ORIGEN', 'ID_DESCRIPCION_EVENTO', 'FECHA_DESCRIPCION', 'DESCRIPCION', 'ID_OBJETO_INVOLUCRADO', 'OBSERVACIONES', 'ID_OBJETO', 'CANTIDAD', 'VALOR_ESTIMADO', 'ID_VEHICULO_INVOLUCRADO', 'NUMERO_PLACA', 'SENIAS_PARTICULARES', 'ID_COLOR', 'ID_TIPO_VEHICULO', 'ID_ESTADO_ORIGEN', 'ID_VEHICULO_ORIGEN', 'ID_USO_VEHICULO', 'ID_ESTADO_FISICO_VEHICULO', 'NUMERO_TELEFONO', 'FOLIO', 'ID_DISPOSITIVO', 'FECHA_INICIO', 'FECHA_FIN', 'ID_MOTIVO', 'PRIORIDAD', 'FECHA_EVENTO']
Seleccione la lista a filtrar:
ID_MUNICIPIO
Elementos unicos de la lista: ['MIGUEL HIDALGO', 'TLAHUAC', 'ALVARO OBREGON', 'IZTACALCO', 'COYOACAN', 'GUSTAVO A. MADERO', 'IZTAPALAPA', 'CUAUHTEMOC', 'BENITO JUAREZ', 'AZCAPOTZALC

In [ ]:
mapa=mapas_calor(df,tiles[3],geo_s=True,geo_c=False,geo_a=False)
mapa



Listas a filtrar: ['Unnamed: 0', 'ID_EVENTO', 'ID_DIRECCION_EVENTO', 'ID_COLONIA', 'ID_MUNICIPIO', 'ID_ESTADO', 'LATITUD', 'LONGITUD', 'LUGAR', 'CALLE', 'CODIGO_POSTAL', 'ID_PERSONA_INVOLUCRADA', 'NOMBRE', 'APELLIDO_PATERNO', 'APELLIDO_MATERNO', 'SEXO', 'EDAD', 'FECHA_MODIFICACION', 'ID_TIPO_PERSONA', 'ID_PERSONA_ORIGEN', 'ID_DESCRIPCION_EVENTO', 'FECHA_DESCRIPCION', 'DESCRIPCION', 'ID_OBJETO_INVOLUCRADO', 'OBSERVACIONES', 'ID_OBJETO', 'CANTIDAD', 'VALOR_ESTIMADO', 'ID_VEHICULO_INVOLUCRADO', 'NUMERO_PLACA', 'SENIAS_PARTICULARES', 'ID_COLOR', 'ID_TIPO_VEHICULO', 'ID_ESTADO_ORIGEN', 'ID_VEHICULO_ORIGEN', 'ID_USO_VEHICULO', 'ID_ESTADO_FISICO_VEHICULO', 'NUMERO_TELEFONO', 'FOLIO', 'ID_DISPOSITIVO', 'FECHA_INICIO', 'FECHA_FIN', 'ID_MOTIVO', 'PRIORIDAD', 'FECHA_EVENTO']
Seleccione la lista a filtrar:
NOMBRE
Elementos unicos de la lista: ['VIOLETA', 'HELIBERTO', 'MARTIN JUAN', 'MARIA CHRISTINA', 'EULOGIO', 'MARIA SALUD', 'LAZARO', 'GREGORIO', 'JOAQUIN', 'ESTEFANY', 'IRMA', 'ARMANDO', 'CHRISTI

In [ ]:
mapa=mapas_coropleta_mer(tiles[4],fill_color[6])
mapa

Listas a filtrar: ['Unnamed: 0', 'ID_EVENTO', 'ID_DIRECCION_EVENTO', 'ID_COLONIA', 'ID_MUNICIPIO', 'ID_ESTADO', 'LATITUD', 'LONGITUD', 'LUGAR', 'CALLE', 'CODIGO_POSTAL', 'ID_PERSONA_INVOLUCRADA', 'NOMBRE', 'APELLIDO_PATERNO', 'APELLIDO_MATERNO', 'SEXO', 'EDAD', 'FECHA_MODIFICACION', 'ID_TIPO_PERSONA', 'ID_PERSONA_ORIGEN', 'ID_DESCRIPCION_EVENTO', 'FECHA_DESCRIPCION', 'DESCRIPCION', 'ID_OBJETO_INVOLUCRADO', 'OBSERVACIONES', 'ID_OBJETO', 'CANTIDAD', 'VALOR_ESTIMADO', 'ID_VEHICULO_INVOLUCRADO', 'NUMERO_PLACA', 'SENIAS_PARTICULARES', 'ID_COLOR', 'ID_TIPO_VEHICULO', 'ID_ESTADO_ORIGEN', 'ID_VEHICULO_ORIGEN', 'ID_USO_VEHICULO', 'ID_ESTADO_FISICO_VEHICULO', 'NUMERO_TELEFONO', 'FOLIO', 'ID_DISPOSITIVO', 'FECHA_INICIO', 'FECHA_FIN', 'ID_MOTIVO', 'PRIORIDAD', 'FECHA_EVENTO']
Seleccione la lista a filtrar:
SEXO
Elementos unicos de la lista: [2.0, 1.0]
Patron a encontrar:
2.0


In [ ]:
mapa=mapas_calor_time(tiles[1])
mapa

Listas a filtrar: ['Unnamed: 0', 'ID_EVENTO', 'ID_DIRECCION_EVENTO', 'ID_COLONIA', 'ID_MUNICIPIO', 'ID_ESTADO', 'LATITUD', 'LONGITUD', 'LUGAR', 'CALLE', 'CODIGO_POSTAL', 'ID_PERSONA_INVOLUCRADA', 'NOMBRE', 'APELLIDO_PATERNO', 'APELLIDO_MATERNO', 'SEXO', 'EDAD', 'FECHA_MODIFICACION', 'ID_TIPO_PERSONA', 'ID_PERSONA_ORIGEN', 'ID_DESCRIPCION_EVENTO', 'FECHA_DESCRIPCION', 'DESCRIPCION', 'ID_OBJETO_INVOLUCRADO', 'OBSERVACIONES', 'ID_OBJETO', 'CANTIDAD', 'VALOR_ESTIMADO', 'ID_VEHICULO_INVOLUCRADO', 'NUMERO_PLACA', 'SENIAS_PARTICULARES', 'ID_COLOR', 'ID_TIPO_VEHICULO', 'ID_ESTADO_ORIGEN', 'ID_VEHICULO_ORIGEN', 'ID_USO_VEHICULO', 'ID_ESTADO_FISICO_VEHICULO', 'NUMERO_TELEFONO', 'FOLIO', 'ID_DISPOSITIVO', 'FECHA_INICIO', 'FECHA_FIN', 'ID_MOTIVO', 'PRIORIDAD', 'FECHA_EVENTO']
Seleccione la lista a filtrar:
CALLE
Elementos unicos de la lista: ['LAGO DE FONDO', 'MIGUEL NEGRETE', 'CERRADA SANTA LUCÍA', 'PUENTE DE LA GLORIA', 'CALLE 4', 'TOLTECAS', 'TESORO', 'FRANCISCO SARABIA', 'RETORNO PRIMERO CASA 

## Extras 

